In [27]:
import pandas as pd
import numpy as np
from scapy.all import PacketList,rdpcap, TCP,IP,UDP
from pathlib import Path
from collections import defaultdict
from datetime import datetime, timedelta
import os
import matplotlib.pyplot as plt
import pickle
import torch

In [28]:
# Read all the pcap files available along with the mac address of the corresponding device
packets = PacketList()
pathlist = Path('captures_IoT-Sentinel').glob('**/Setup-C-*.pcap')
for path in pathlist:
    # because path is object not string
    path_in_str = str(path)
    #print("Name of the device : " + path_in_str.split('/')[-2])
    parent_path = os.path.dirname(path_in_str)   
    mac = open(parent_path + '/_iotdevice-mac.txt', 'r').read().strip()
    newpackets = rdpcap(path_in_str)
    for packet in newpackets:
        packet.device = path_in_str.split('/')[-2] # set the device name for each entry 
    packets = packets + newpackets

packets = packets.filter(lambda x: x.haslayer(TCP)) # filter only TCP packets; Not sure if we should use this or not at this point

print(packets.show())





0000 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http S
0001 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http A
0002 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http PA / Raw
0003 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:46613 A
0004 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:46613 PA / Raw
0005 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http A
0006 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:46613 FPA / Raw
0007 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http A
0008 Ether / IP / TCP 10.10.10.30:46613 > 10.10.10.6:http FA
0009 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:46613 A
0010 Ether / IP / TCP 10.10.10.30:52401 > 10.10.10.6:http S
0011 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:52401 SA
0012 Ether / IP / TCP 10.10.10.30:52401 > 10.10.10.6:http A
0013 Ether / IP / TCP 10.10.10.30:52401 > 10.10.10.6:http PA / Raw
0014 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:52401 A
0015 Ether / IP / TCP 10.10.10.6:http > 10.10.10.30:52401 PA / Raw
00

In [ ]:
print(packets[0].show())

In [57]:
for pkt in packets:
    if hasattr(pkt, 'device'):
        x = 0
    else:
        print('No device attribute')

In [ ]:

# Read the pcap file !! Only for one file and testing purpose

dir = 'captures_IoT-Sentinel/Aria/Setup-A-1-STA.pcap'
parent_dir = os.path.dirname(dir) # get the parent directory

packets = rdpcap(dir)
mac = open(parent_dir + '/_iotdevice-mac.txt', 'r').read().strip()
print(mac)

print(len(packets))
packets = packets.filter(lambda x: x.haslayer(TCP)) # filter only TCP packets Not sure if we should use this or not
print(len(packets))



In [29]:
# Aggregate packets into flows

flows = defaultdict(list)

for pkt in packets:

    if IP in pkt and (TCP in pkt or UDP in pkt):
       
        flow_key = (
            pkt[IP].src,
            pkt[IP].dst,
            pkt.sport,
            pkt.dport,
            pkt[IP].proto,
            pkt.device
        )
        
        flows[flow_key].append(pkt)
    

for flow, pkts in flows.items():
    print(f"Flow {flow} has {len(pkts)} packets and device is {pkts[0].device} and has number of bytes {sum([pkt.len for pkt in pkts])}")


Flow ('10.10.10.30', '10.10.10.6', 46613, 80, 6, 'HueSwitch') has 6 packets and device is HueSwitch and has number of bytes 522
Flow ('10.10.10.6', '10.10.10.30', 80, 46613, 6, 'HueSwitch') has 4 packets and device is HueSwitch and has number of bytes 1093
Flow ('10.10.10.30', '10.10.10.6', 52401, 80, 6, 'HueSwitch') has 6 packets and device is HueSwitch and has number of bytes 522
Flow ('10.10.10.6', '10.10.10.30', 80, 52401, 6, 'HueSwitch') has 5 packets and device is HueSwitch and has number of bytes 1153
Flow ('10.10.10.30', '10.10.10.6', 48436, 80, 6, 'HueSwitch') has 6 packets and device is HueSwitch and has number of bytes 522
Flow ('10.10.10.6', '10.10.10.30', 80, 48436, 6, 'HueSwitch') has 5 packets and device is HueSwitch and has number of bytes 1153
Flow ('10.10.10.30', '10.10.10.6', 43432, 80, 6, 'HueSwitch') has 6 packets and device is HueSwitch and has number of bytes 522
Flow ('10.10.10.6', '10.10.10.30', 80, 43432, 6, 'HueSwitch') has 5 packets and device is HueSwitch a

In [30]:
# Currently we use these features only : src_port; dst_port; proto; num_pkts; num_bytes; device = label;

input = np.zeros((1,5))
target = np.zeros((1,1))
for flow,pkts in flows.items():
    #print(flow[2], flow[3], flow[4], len(pkts), sum([pkt.len for pkt in pkts]), pkts[0].device)
    input = np.vstack([input,(flow[2], flow[3], flow[4], len(pkts), sum([pkt.len for pkt in pkts]))])
    target = np.vstack([target,pkts[0].device])

input = np.delete(input, 0, axis=0)
target = np.delete(target, 0, axis=0)
print(input) 


[[4.6613e+04 8.0000e+01 6.0000e+00 6.0000e+00 5.2200e+02]
 [8.0000e+01 4.6613e+04 6.0000e+00 4.0000e+00 1.0930e+03]
 [5.2401e+04 8.0000e+01 6.0000e+00 6.0000e+00 5.2200e+02]
 ...
 [8.0000e+01 4.0651e+04 6.0000e+00 6.0000e+00 5.7500e+02]
 [4.0652e+04 8.0000e+01 6.0000e+00 7.0000e+00 1.1640e+03]
 [8.0000e+01 4.0652e+04 6.0000e+00 6.0000e+00 5.7500e+02]]


In [31]:
# make the labels more generic not brand names

label_mapping = {
    'Aria' : 'Device',
'D-LinkCam' : 'IP Camera',
'D-LinkDayCam' : 'IP Camera',
'D-LinkDoorSensor' : 'Sensor',
'D-LinkHomeHub' : 'Hub',
'D-LinkSensor' : 'Sensor',
'D-LinkSiren' : 'Alarm',
'D-LinkSwitch' : 'Switch',
'D-LinkWaterSensor' : 'Sensor',
'EdimaxCam1' : 'IP Camera',
'EdimaxCam2' : 'IP Camera',
'EdimaxPlug1101W' : 'Plug',
'EdimaxPlug2101W' : 'Plug',
'EdnetCam1' : 'IP Camera',
'EdnetCam2' : 'IP Camera',
'EdnetGateway' : 'Gateway',
'HomeMaticPlug' : 'Plug',
'HueBridge' : 'Hub',
'HueSwitch' : 'Switch',
'Lightify' : 'Lighting',
'MAXGateway' : 'Gateway',
'SmarterCoffee' : 'Appliance',
'TP-LinkPlugHS100' : 'Plug',
'TP-LinkPlugHS110' : 'Plug',
'WeMoInsightSwitch' : 'Switch',
'WeMoInsightSwitch2' : 'Switch',
'WeMoLink' : 'Hub',
'WeMoSwitch' : 'Switch',
'WeMoSwitch2' : 'Switch',
'Withings' : 'Device',
'iKettle2' : 'Appliance',

}


In [32]:
# Map the old labels to the new ones
y_mapped = pd.Series(target.ravel()).map(label_mapping)

y_mapped = y_mapped.values.reshape(-1, 1)

print(len(y_mapped))
print(len(target))
print(y_mapped)


9072
9072
[['Switch']
 ['Switch']
 ['Switch']
 ...
 ['Hub']
 ['Hub']
 ['Hub']]


In [33]:
data = pd.DataFrame(input, columns=['src', 'dst', 'proto', 'num_pkts', 'num_bytes'])
data['device'] = y_mapped.flatten()

label_counts = data['device'].value_counts()

# Filter out labels with fewer than 50 occurrences - to have more data points
valid_labels = label_counts[label_counts >= 50].index
valid_labels = valid_labels[valid_labels != 'Alarm'] # Drop these because the dataset is not accurate enough
valid_labels = valid_labels[valid_labels != 'Sensor'] #
filtered_data = data[data['device'].isin(valid_labels)]

print(filtered_data['device'].value_counts())

# Find the minimum number of samples across labels so that we can balance the dataset - have equal number of samples for each class
min_count = filtered_data['device'].value_counts().min()
balanced_data = filtered_data.groupby('device').sample(n=min_count, random_state=42)

X_balanced = balanced_data[['src', 'dst', 'proto', 'num_pkts', 'num_bytes']].values
y_balanced = balanced_data['device'].values



device
Switch       3934
Hub          3472
Plug          200
Gateway       104
IP Camera      54
Name: count, dtype: int64


In [34]:
# Split the dataset into training and testing set - currently 80-20 split
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X_balanced, y_balanced, test_size=0.2, random_state=42)

In [35]:
from sklearn.ensemble import RandomForestClassifier

clf = RandomForestClassifier()
clf.fit(X_train, y_train)



RandomForestClassifier()

In [36]:
from sklearn.metrics import classification_report, precision_score, recall_score

#y_pred = clf.predict(X_test)

probabilities = clf.predict_proba(X_test)

threshold = 0.5

max_prob_indices = np.argmax(probabilities, axis=1)

# Get the maximum probability for each prediction
max_probs = np.max(probabilities, axis=1)

# Original predictions
predictions = clf.predict(X_test)

# Add 'other' label where max probability is below the threshold
for i, prob in enumerate(max_probs):
    if prob < threshold:
        predictions[i] = 'other'


print("Classification Report:\n", classification_report(y_test, predictions))



Classification Report:
               precision    recall  f1-score   support

     Gateway       1.00      1.00      1.00        11
         Hub       0.62      0.56      0.59         9
   IP Camera       0.93      1.00      0.96        13
        Plug       1.00      0.78      0.88         9
      Switch       0.75      0.75      0.75        12
       other       0.00      0.00      0.00         0

    accuracy                           0.83        54
   macro avg       0.72      0.68      0.70        54
weighted avg       0.86      0.83      0.85        54



/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
/opt/anaconda3/lib/python3.12/site-packages/sklearn/metrics/_classification.py:1531: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


In [20]:
importances = clf.feature_importances_
print("Feature importances:", importances)

# Visualize the feature importances
features = ['src', 'dst', 'proto', 'num_pkts', 'num_bytes'] 
plt.bar(features, importances)
plt.xlabel('Features')
plt.ylabel('Importance')
plt.title('Feature Importances')
plt.show()

Feature importances: [0.20474718 0.22825661 0.         0.20824755 0.35874867]


In [38]:
with open('rf_classifier.pkl', 'wb') as f:
    pickle.dump(clf, f)

In [16]:
# Get the counts of the flows of each device

devices = np.unique([pkt.device for pkts in flows.values() for pkt in pkts ])
counts = {device: 0 for device in devices}

for device in devices:
    counts[device] = sum([len(pkts) for flow, pkts in flows.items() if pkts[0].device == device])



In [22]:
# generate the input labels for the packet level one
# Currently these features src ip; dst ip; src port; dst port; packet size; ack number; flag; device is the target label


dt = np.zeros((1,6))
label = np.zeros((1,1))
for packet in packets:
    dt = np.vstack([dt, [packet[IP].src, packet[IP].dst, packet[TCP].sport, packet[TCP].dport, packet.len, packet[TCP].flags.value]])
    label = np.vstack([label,packet.device])

dt = np.delete(dt, 0, axis=0)
label = np.delete(label, 0, axis=0)
print(dt) 


[['10.10.10.30' '10.10.10.6' '46613' '80' '60' '2']
 ['10.10.10.30' '10.10.10.6' '46613' '80' '52' '16']
 ['10.10.10.30' '10.10.10.6' '46613' '80' '254' '24']
 ...
 ['130.211.93.93' '10.10.10.6' '80' '40652' '52' '17']
 ['10.10.10.6' '130.211.93.93' '40652' '80' '52' '16']
 ['130.211.93.93' '10.10.10.6' '80' '40652' '52' '16']]


In [23]:
# Map the old labels to the new ones
label_mapped = pd.Series(label.ravel()).map(label_mapping)

label_mapped = label_mapped.values.reshape(-1, 1)

print(label_mapped)


[['Switch']
 ['Switch']
 ['Switch']
 ...
 ['Hub']
 ['Hub']
 ['Hub']]


In [24]:
train_data = pd.DataFrame(dt, columns=['src', 'dst', 'inp_prt', 'out_port', 'num_bytes', 'flag'])
train_data['device'] = label_mapped.flatten()

label_counts = train_data['device'].value_counts()

# Filter out labels with fewer than 100 occurrences - to have more data points
valid_labels = label_counts[label_counts >= 100].index
filtered_data = train_data[train_data['device'].isin(valid_labels)]

print(filtered_data['device'].value_counts())

# Find the minimum number of samples across labels so that we can balance the dataset - have equal number of samples for each class
min_count = filtered_data['device'].value_counts().min()
balanced_data = filtered_data.groupby('device').sample(n=min_count, random_state=42)

X_balanced_data = balanced_data[['src', 'dst', 'inp_prt', 'out_port', 'num_bytes', 'flag']].values
y_balanced_data = balanced_data['device'].values


device
Switch       34633
Hub          27580
Sensor       17113
Alarm         8706
Plug          3264
Device        1431
Gateway       1020
IP Camera      715
Name: count, dtype: int64
